## Income Prediction with Spark Random Forest

### Install findspark and init

In [3]:
!pip install findspark

In [4]:
import findspark
findspark.init()

### Get spark and h2o sessions

In [5]:
from pyspark.sql import SparkSession
from pysparkling import H2OContext
import h2o

from pyspark.sql import SparkSession
spark = (
    SparkSession.builder.appName('cognetix-spark-nb')
    .config('spark.dynamicAllocation.enabled', 'false')
    .getOrCreate()
)
spark.sparkContext.setLogLevel("ERROR")
sc = spark.sparkContext
hc = H2OContext.getOrCreate()
h2o_cluster = h2o.cluster()

23/10/20 20:37:19 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/10/20 20:37:20 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.


10-20 20:37:25.955 172.17.0.2:54325      19675    Thread-4  INFO water.default: ----- H2O started  -----
10-20 20:37:25.956 172.17.0.2:54325      19675    Thread-4  INFO water.default: Build git branch: rel-zz_kurka
10-20 20:37:25.956 172.17.0.2:54325      19675    Thread-4  INFO water.default: Build git hash: 5ff8870f912c6110d7b6988f577c020de10496ec
10-20 20:37:25.956 172.17.0.2:54325      19675    Thread-4  INFO water.default: Build git describe: jenkins-3.40.0.3-122-g5ff8870
10-20 20:37:25.957 172.17.0.2:54325      19675    Thread-4  INFO water.default: Build project version: 3.40.0.4
10-20 20:37:25.957 172.17.0.2:54325      19675    Thread-4  INFO water.default: Build age: 5 months and 22 days
10-20 20:37:25.957 172.17.0.2:54325      19675    Thread-4  INFO water.default: Built by: 'jenkins'
10-20 20:37:25.957 172.17.0.2:54325      19675    Thread-4  INFO water.default: Built on: '2023-04-28 12:08:23'
10-20 20:37:25.957 172.17.0.2:54325      19675    Thread-4  WARN water.default: 


--------------------------  ----------------------------------------
H2O_cluster_uptime:         14 secs
H2O_cluster_timezone:       Etc/UTC
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.40.0.4
H2O_cluster_version_age:    5 months and 22 days
H2O_cluster_name:           sparkling-water-root_local-1697834240745
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    1 Gb
H2O_cluster_total_cores:    4
H2O_cluster_allowed_cores:  4
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://5b5a8eb7561c:54324
H2O_connection_proxy:       null
H2O_internal_security:      False
Python_version:             3.9.7 final
--------------------------  ----------------------------------------


Sparkling Water Context:
 * Sparkling Water Version: 3.40.0.4-1-3.1
 * H2O name: sparkling-water-root_local-1697834240745
 * cluster size: 1
 * list of used nodes:
  (executorId, host, port)
  ------------------------
  (0,172.17.0.2,54325)
  ------------------------

  Open H2O Flow in browser: http://5b5a8eb7561c:54324 (CMD + click in Mac OSX)

    


### Global params

In [6]:
seed = 42

train_path = '../data/census-train.csv'
test_path = '../data/census-test.csv'
model_path = 'outputs/income_rf_spark'
pred_path = 'outputs/income_rf_spark_pred'

### Data Prep

In [7]:
from pyspark.sql.types import StructType
from pyspark.sql.types import StructField
from pyspark.sql.functions import col
from pyspark.sql.functions import when
from pyspark.sql.functions import lit
from pyspark.sql.types import StringType
from pyspark.sql.types import IntegerType
from pyspark.sql.types import DoubleType

schema = StructType([
    StructField("age", IntegerType(), True),
    StructField("workclass", StringType(), True),
    StructField("fnlwgt", DoubleType(), True),
    StructField("education", StringType(), True),
    StructField("education_num", IntegerType(), True),
    StructField("marital_status", StringType(), True),
    StructField("occupation", StringType(), True),
    StructField("relationship", StringType(), True),
    StructField("race", StringType(), True),
    StructField("sex", StringType(), True),
    StructField("capital_gain", DoubleType(), True),
    StructField("capital_loss", DoubleType(), True),
    StructField("hours_per_week", DoubleType(), True),
    StructField("native_country", StringType(), True),
    StructField("income_level", StringType(), True),
])

train_df = (
    spark.read
    .format('csv')
    .option('header', 'false')
    .option('delimiter', ',')
    .schema(schema)
    .load(train_path)
    .drop('education_num')
    .withColumn('label', when(col('income_level').contains('>50K'), lit(1)).otherwise(lit(0)))
    .drop('income_level')
    .withColumn('workclass', when(col('workclass') == ' ?', lit('NA')).otherwise(col('workclass')))
    .withColumn('occupation', when(col('occupation') == ' ?', lit('NA')).otherwise(col('occupation')))
    .withColumn('native_country', when(col('native_country') == ' ?', lit('NA')).otherwise(col('native_country')))
)

test_df = (
    spark.read
    .format('csv')
    .option('header', 'false')
    .option('delimiter', ',')
    .schema(schema)
    .load(test_path)
    .withColumn('label', when(col('income_level').contains('>50K'), lit(1)).otherwise(lit(0)))
    .drop('education_num', 'income_level')
    .withColumn('workclass', when(col('workclass') == ' ?', lit('NA')).otherwise(col('workclass')))
    .withColumn('occupation', when(col('occupation') == ' ?', lit('NA')).otherwise(col('occupation')))
    .withColumn('native_country', when(col('native_country') == ' ?', lit('NA')).otherwise(col('native_country')))
)

10-20 20:37:41.510 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.execution.datasources.InMemoryFileIndex: It took 76 ms to list leaf files for 1 paths.
10-20 20:37:42.898 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.execution.datasources.InMemoryFileIndex: It took 2 ms to list leaf files for 1 paths.


### ML Pipeline

#### Preprocessing

In [8]:
train_hdf = hc.asH2OFrame(train_df)
train_hdf['label'] = train_hdf['label'].asfactor()
train_hdf['workclass'] = train_hdf['workclass'].asfactor()
train_hdf['education'] = train_hdf['education'].asfactor()
train_hdf['marital_status'] = train_hdf['marital_status'].asfactor()
train_hdf['occupation'] = train_hdf['occupation'].asfactor()
train_hdf['relationship'] = train_hdf['relationship'].asfactor()
train_hdf['race'] = train_hdf['race'].asfactor()
train_hdf['sex'] = train_hdf['sex'].asfactor()
train_hdf['native_country'] = train_hdf['native_country'].asfactor()

10-20 20:37:43.447 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.execution.datasources.FileSourceStrategy: Pushed Filters: 
10-20 20:37:43.448 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.execution.datasources.FileSourceStrategy: Post-Scan Filters: 
10-20 20:37:43.451 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.execution.datasources.FileSourceStrategy: Output Data Schema: struct<age: int, workclass: string, fnlwgt: double, education: string, marital_status: string ... 12 more fields>
10-20 20:37:44.164 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.catalyst.expressions.codegen.CodeGenerator: Code generated in 264.720999 ms
10-20 20:37:44.206 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.storage.memory.MemoryStore: Block broadcast_0 stored as values in memory (estimated size 176.1 KiB, free 434.2 MiB)
10-20 20:37:44.260 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sto

10-20 20:37:45.436 172.17.0.2:54325      19675  .0 (TID 0)  INFO org.apache.spark.executor.Executor: Finished task 0.0 in stage 0.0 (TID 0). 1787 bytes result sent to driver
10-20 20:37:45.442 172.17.0.2:54325      19675  t-getter-0  INFO org.apache.spark.scheduler.TaskSetManager: Finished task 0.0 in stage 0.0 (TID 0) in 735 ms on 5b5a8eb7561c (executor driver) (1/1)
10-20 20:37:45.444 172.17.0.2:54325      19675  t-getter-0  INFO org.apache.spark.scheduler.TaskSchedulerImpl: Removed TaskSet 0.0, whose tasks have all completed, from pool 
10-20 20:37:45.449 172.17.0.2:54325      19675  event-loop  INFO org.apache.spark.scheduler.DAGScheduler: ResultStage 0 (fold at PartitionStatsGenerator.scala:35) finished in 0.897 s
10-20 20:37:45.452 172.17.0.2:54325      19675  event-loop  INFO org.apache.spark.scheduler.DAGScheduler: Job 0 is finished. Cancelling potential speculative or zombie tasks for this job
10-20 20:37:45.452 172.17.0.2:54325      19675  event-loop  INFO org.apache.spark.sc

10-20 20:37:46.100 172.17.0.2:54325      19675  .0 (TID 1)  INFO ai.h2o.sparkling.backend.H2OChunk: H2O node http://172.17.0.2:54325/3/Chunk?frame_name=frame_rdd_5-1616263956&num_rows=32561&compression=SNAPPY&maximum_vector_sizes=&expected_types=BAsHCwsLCwsLBwcHCwQ%3D&chunk_id=0 successfully responded for the PUT.
10-20 20:37:46.108 172.17.0.2:54325      19675  .0 (TID 1)  INFO ai.h2o.sparkling.backend.H2OChunk: H2O node http://172.17.0.2:54325/3/ChunkCategoricalDomains?frame_name=frame_rdd_5-1616263956&chunk_id=0&compression=SNAPPY successfully responded for the PUT.
10-20 20:37:46.108 172.17.0.2:54325      19675  .0 (TID 1)  INFO ai.h2o.sparkling.backend.H2OChunk: H2O node http://172.17.0.2:54325/3/ChunkCategoricalDomains?frame_name=frame_rdd_5-1616263956&chunk_id=0&compression=SNAPPY successfully responded for the PUT.
10-20 20:37:46.110 172.17.0.2:54325      19675  .0 (TID 1)  INFO org.apache.spark.executor.Executor: Finished task 0.0 in stage 1.0 (TID 1). 1635 bytes result sent to

In [9]:
test_hdf = hc.asH2OFrame(test_df)
test_hdf['label'] = test_hdf['label'].asfactor()
test_hdf['workclass'] = test_hdf['workclass'].asfactor()
test_hdf['education'] = test_hdf['education'].asfactor()
test_hdf['marital_status'] = test_hdf['marital_status'].asfactor()
test_hdf['occupation'] = test_hdf['occupation'].asfactor()
test_hdf['relationship'] = test_hdf['relationship'].asfactor()
test_hdf['race'] = test_hdf['race'].asfactor()
test_hdf['sex'] = test_hdf['sex'].asfactor()
test_hdf['native_country'] = test_hdf['native_country'].asfactor()

10-20 20:37:46.495 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.execution.datasources.FileSourceStrategy: Pushed Filters: 
10-20 20:37:46.496 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.execution.datasources.FileSourceStrategy: Post-Scan Filters: 
10-20 20:37:46.496 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.sql.execution.datasources.FileSourceStrategy: Output Data Schema: struct<age: int, workclass: string, fnlwgt: double, education: string, marital_status: string ... 12 more fields>
10-20 20:37:46.510 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.storage.memory.MemoryStore: Block broadcast_3 stored as values in memory (estimated size 176.1 KiB, free 434.0 MiB)
10-20 20:37:46.529 172.17.0.2:54325      19675    Thread-4  INFO org.apache.spark.storage.memory.MemoryStore: Block broadcast_3_piece0 stored as bytes in memory (estimated size 28.0 KiB, free 434.0 MiB)
10-20 20:37:46.530 172.17.0.2:54325      196

#### XGB GridSearch

In [12]:
from h2o.estimators import H2OXGBoostEstimator
from h2o.grid import H2OGridSearch
x = [x for x in list(train_hdf.columns) if x != 'label']
y = 'label'

hyper_params_tune = {
    'ntrees': [100, 150, 200],
    'max_depth': [8, 10, 15],
    'min_rows': [80, 125, 200]
}

search_criteria_tune = {
    'strategy': 'RandomDiscrete',
    'max_runtime_secs': 180,
    'max_models': 5,
    'seed': seed,
    'stopping_rounds': 5,
    'stopping_metric': 'auc',
    'stopping_tolerance': 1e-3
}
final_grid = H2OXGBoostEstimator(
    learn_rate=0.05,
    sample_rate=0.7,
    col_sample_rate_per_tree=0.2,
    seed=seed
)
model_grid = H2OGridSearch(final_grid, hyper_params=hyper_params_tune, search_criteria=search_criteria_tune)
model_grid.train(x=x, y=y, training_frame=train_hdf, validation_frame=test_hdf)

10-20 20:38:17.398 172.17.0.2:54325      19675  7476791-68  INFO water.default: POST /4/sessions, parms: {}
10-20 20:38:17.988 172.17.0.2:54325      19675  7476791-69  INFO water.default: POST /99/Rapids, parms: {ast=(tmp= py_9_sid_8ba3 (:= (tmp= py_8_sid_8ba3 (:= (tmp= py_7_sid_8ba3 (:= (tmp= py_6_sid_8ba3 (:= (tmp= py_5_sid_8ba3 (:= (tmp= py_4_sid_8ba3 (:= (tmp= py_3_sid_8ba3 (:= (tmp= py_2_sid_8ba3 (:= (tmp= py_1_sid_8ba3 (:= frame_rdd_5-1616263956 (as.factor (cols_py frame_rdd_5-1616263956 'label')) 13 [])) (as.factor (cols_py py_1_sid_8ba3 'workclass')) 1 [])) (as.factor (cols_py py_2_sid_8ba3 'education')) 3 [])) (as.factor (cols_py py_3_sid_8ba3 'marital_status')) 4 [])) (as.factor (cols_py py_4_sid_8ba3 'occupation')) 5 [])) (as.factor (cols_py py_5_sid_8ba3 'relationship')) 6 [])) (as.factor (cols_py py_6_sid_8ba3 'race')) 7 [])) (as.factor (cols_py py_7_sid_8ba3 'sex')) 8 [])) (as.factor (cols_py py_8_sid_8ba3 'native_country')) 12 [])), session_id=_sid_8ba3}
10-20 20:38:18.6

[20:38:19] WARNING: /dot/src/gbm/gbtree.cc:73: DANGER AHEAD: You have manually specified `updater` parameter. The `tree_method` parameter will be ignored. Incorrect sequence of updaters will produce undefined behavior. For common uses, we recommend using`tree_method` parameter instead.
[20:38:19] WARNING: /dot/src/learner.cc:207: No visible GPU is found, setting `gpu_id` to -1


10-20 20:38:19.108 172.17.0.2:54325      19675      FJ-2-7  INFO hex.tree.xgboost.XGBoost: fill ratio: 0.10401813763211365
10-20 20:38:19.111 172.17.0.2:54325      19675      FJ-2-7  INFO hex.tree.xgboost.XGBoost: Need to score validation frame by XGBoost native backend: false
10-20 20:38:19.116 172.17.0.2:54325      19675      FJ-2-7  INFO hex.tree.xgboost.XGBoostModel: Using CPU backend.
10-20 20:38:19.116 172.17.0.2:54325      19675      FJ-2-7  INFO hex.tree.xgboost.XGBoostModel: Using exact tree method.
10-20 20:38:19.118 172.17.0.2:54325      19675      FJ-2-7  INFO hex.tree.xgboost.XGBoostModel: XGBoost Parameters:
10-20 20:38:19.118 172.17.0.2:54325      19675      FJ-2-7  INFO hex.tree.xgboost.XGBoostModel:  colsample_bytree = 0.2
10-20 20:38:19.118 172.17.0.2:54325      19675      FJ-2-7  INFO hex.tree.xgboost.XGBoostModel:  silent = true
10-20 20:38:19.118 172.17.0.2:54325      19675      FJ-2-7  INFO hex.tree.xgboost.XGBoostModel:  tree_method = exact
10-20 20:38:19.118 172

Hyper-Parameter Search Summary: ordered by increasing logloss
    max_depth    min_rows    ntrees    model_ids                                                        logloss
--  -----------  ----------  --------  ---------------------------------------------------------------  ---------
    8            80          200       Grid_XGBoost_py_9_sid_8ba3_model_python_1697834243212_1_model_5  0.309984
    15           80          150       Grid_XGBoost_py_9_sid_8ba3_model_python_1697834243212_1_model_2  0.316157
    15           200         200       Grid_XGBoost_py_9_sid_8ba3_model_python_1697834243212_1_model_4  0.326701
    15           80          100       Grid_XGBoost_py_9_sid_8ba3_model_python_1697834243212_1_model_1  0.329372
    15           200         150       Grid_XGBoost_py_9_sid_8ba3_model_python_1697834243212_1_model_3  0.331576

In [13]:
grid_perf_sorted = model_grid.get_grid(sort_by='auc', decreasing=True)

10-20 20:39:47.194 172.17.0.2:54325      19675  7476791-65  INFO water.default: GET /99/Grids/Grid_XGBoost_py_9_sid_8ba3_model_python_1697834243212_1, parms: {sort_by=auc, decreasing=True}
10-20 20:39:47.236 172.17.0.2:54325      19675  7476791-65  INFO water.default: Hyper-Parameter Search Summary (ordered by decreasing auc):
10-20 20:39:47.236 172.17.0.2:54325      19675  7476791-65  INFO water.default:   max_depth   min_rows  ntrees                                                        model_ids      auc
10-20 20:39:47.236 172.17.0.2:54325      19675  7476791-65  INFO water.default:           8   80.00000     200  Grid_XGBoost_py_9_sid_8ba3_model_python_1697834243212_1_model_5  0.91022
10-20 20:39:47.236 172.17.0.2:54325      19675  7476791-65  INFO water.default:          15   80.00000     150  Grid_XGBoost_py_9_sid_8ba3_model_python_1697834243212_1_model_2  0.90883
10-20 20:39:47.236 172.17.0.2:54325      19675  7476791-65  INFO water.default:          15   80.00000     100  Grid

In [15]:
best_model = grid_perf_sorted.models[0]

In [20]:
grid_perf_sorted.sorted_metric_table()

max_depth  min_rows  ntrees  \
0         15.0      80.0   150.0   
1          8.0     100.0   200.0   
2         10.0     150.0   150.0   
3         10.0     100.0   100.0   
4          8.0     200.0   100.0   

                                           model_ids       auc  
0  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.923286  
1  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.922359  
2  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.920551  
3  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.920419  
4  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.917633

#### GBM GridSearch

In [17]:
from h2o.estimators import H2OGradientBoostingEstimator
from h2o.grid import H2OGridSearch
cols = [x for x in list(train_hdf.columns) if x != 'label']
y = 'label'

hyper_params_tune = {
    'ntrees': [50, 100, 150, 200],
    'max_depth': [8, 10, 15, 20],
    'min_rows': [80, 100, 150, 200]
}

search_criteria_tune = {
    'strategy': 'RandomDiscrete',
    'max_runtime_secs': 180,
    'max_models': 5,
    'seed': seed,
    'stopping_rounds': 5,
    'stopping_metric': 'auc',
    'stopping_tolerance': 1e-3
}
final_grid = H2OGradientBoostingEstimator(
    learn_rate=0.05,
    learn_rate_annealing=0.99,
    score_tree_interval=10,
    seed=seed
)
model_grid = H2OGridSearch(final_grid, hyper_params=hyper_params_tune, search_criteria=search_criteria_tune)
model_grid.train(x=x, y=y, training_frame=train_hdf, validation_frame=test_hdf)

10-20 20:39:54.988 172.17.0.2:54325      19675  7476791-64  INFO water.default: POST /99/Grid/gbm, parms: {fold_assignment=auto, learn_rate=0.05, nbins=20, max_depth=5, learn_rate_annealing=0.99, min_split_improvement=1e-05, tweedie_power=1.5, nbins_top_level=1024, score_each_iteration=False, calibration_method=auto, hyper_parameters={"ntrees": [50,100,150,200],"max_depth": [8,10,15,20],"min_rows": [80,100,150,200]}, build_tree_one_node=False, keep_cross_validation_predictions=False, auc_type=auto, stopping_metric=auto, ntrees=50, pred_noise_bandwidth=0.0, training_frame=py_9_sid_8ba3, histogram_type=auto, stopping_tolerance=0.001, quantile_alpha=0.5, validation_frame=py_18_sid_8ba3, max_confusion_matrix_size=20, categorical_encoding=auto, stopping_rounds=0, seed=42, parallelism=1, col_sample_rate_change_per_level=1.0, keep_cross_validation_models=True, distribution=auto, search_criteria={"strategy": RandomDiscrete,"max_runtime_secs": 180,"max_models": 5,"seed": 42,"stopping_rounds": 5

Hyper-Parameter Search Summary: ordered by increasing logloss
    max_depth    min_rows    ntrees    model_ids                                                      logloss
--  -----------  ----------  --------  -------------------------------------------------------------  ---------
    15           80          150       Grid_GBM_py_9_sid_8ba3_model_python_1697834243212_372_model_1  0.285997
    8            100         200       Grid_GBM_py_9_sid_8ba3_model_python_1697834243212_372_model_2  0.288977
    10           150         150       Grid_GBM_py_9_sid_8ba3_model_python_1697834243212_372_model_3  0.292075
    10           100         100       Grid_GBM_py_9_sid_8ba3_model_python_1697834243212_372_model_5  0.294248
    8            200         100       Grid_GBM_py_9_sid_8ba3_model_python_1697834243212_372_model_4  0.299689

In [18]:
grid_perf_sorted = model_grid.get_grid(sort_by='auc', decreasing=True)

10-20 20:40:28.088 172.17.0.2:54325      19675  7476791-69  INFO water.default: GET /99/Grids/Grid_GBM_py_9_sid_8ba3_model_python_1697834243212_372, parms: {sort_by=auc, decreasing=True}
10-20 20:40:28.107 172.17.0.2:54325      19675  7476791-69  INFO water.default: Hyper-Parameter Search Summary (ordered by decreasing auc):
10-20 20:40:28.107 172.17.0.2:54325      19675  7476791-69  INFO water.default:   max_depth   min_rows  ntrees                                                      model_ids      auc
10-20 20:40:28.107 172.17.0.2:54325      19675  7476791-69  INFO water.default:          15   80.00000     150  Grid_GBM_py_9_sid_8ba3_model_python_1697834243212_372_model_1  0.92329
10-20 20:40:28.107 172.17.0.2:54325      19675  7476791-69  INFO water.default:           8  100.00000     200  Grid_GBM_py_9_sid_8ba3_model_python_1697834243212_372_model_2  0.92236
10-20 20:40:28.107 172.17.0.2:54325      19675  7476791-69  INFO water.default:          10  150.00000     150  Grid_GBM_py_

In [19]:
best_model = grid_perf_sorted.models[0]

In [21]:
grid_perf_sorted.sorted_metric_table()

max_depth  min_rows  ntrees  \
0         15.0      80.0   150.0   
1          8.0     100.0   200.0   
2         10.0     150.0   150.0   
3         10.0     100.0   100.0   
4          8.0     200.0   100.0   

                                           model_ids       auc  
0  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.923286  
1  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.922359  
2  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.920551  
3  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.920419  
4  Grid_GBM_py_9_sid_8ba3_model_python_1697834243...  0.917633

Closing connection _sid_8ba3 at exit
10-20 20:41:07.835 172.17.0.2:54325      19675  7476791-65  INFO water.default: DELETE /4/sessions/_sid_8ba3, parms: {}
H2O session _sid_8ba3 closed.
